# 银色样式 K 线 Demo
利用 backtesting.py 的可视化结果，演示三种银色风格：
1. 灰银色 K 线且去掉轮廓。
2. 用银色 MA(1) 线完全替代 K 线。
3. 在 2 的基础上，将均线渲染为可调节间距的圆点虚线。

In [1]:
from __future__ import annotations

import sys
from pathlib import Path
from typing import Any, Iterable, Optional, Sequence

import numpy as np
from bokeh.embed import file_html
from bokeh.io import output_notebook
from bokeh.models import CDSView, ColumnDataSource, IndexFilter
from bokeh.resources import INLINE
from IPython.display import HTML, display

import backtesting._plotting as plotting
from backtesting import Backtest

PROJECT_ROOT = Path.cwd().resolve()
if not (PROJECT_ROOT / "run_bear_trap_backtesting.py").exists():
    candidate = PROJECT_ROOT.parent
    if not (candidate / "run_bear_trap_backtesting.py").exists():
        candidate = candidate.parent
    PROJECT_ROOT = candidate.resolve()
if str(PROJECT_ROOT) not in sys.path:
    sys.path.insert(0, str(PROJECT_ROOT))

from run_bear_trap_backtesting import (
    DATA_PATH as RAW_DATA_PATH,
    BearTrapStrategy,
    load_if_data,
    prepare_bear_trap_features,
)

DATA_PATH = (PROJECT_ROOT / RAW_DATA_PATH).resolve()

output_notebook()

C:\Users\nillouise\Music\trade\project\.venv\Lib\site-packages\backtesting\_plotting.py:55: UserWarning: Jupyter Notebook detected. Setting Bokeh output to notebook. This may not work in Jupyter clients without JavaScript support, such as old IDEs. Reset with `backtesting.set_bokeh_output(notebook=False)`.
  warnings.warn('Jupyter Notebook detected. '


Loading BokehJS ...

Loading BokehJS ...

In [2]:
SILVER_BULL = plotting.RGB(192, 192, 192)
SILVER_BEAR = plotting.RGB(158, 158, 158)
LINE_COLOR = "#B0B0B0"
BACKGROUND_COLOR = "#FBFBFB"
DOTTED_DASH_PATTERN: Sequence[int] = (1, 14)
DOTTED_MARKER_STEP = 6


def prepare_backtest(sample_size: int = 400) -> Backtest:
    df = load_if_data(str(DATA_PATH))
    if sample_size:
        df = df.tail(sample_size * 2)
    df = prepare_bear_trap_features(df)
    if sample_size:
        df = df.tail(sample_size)
    bt = Backtest(df, BearTrapStrategy, cash=1_000_000, commission=0.0)
    bt.run()
    return bt


def _candlestick_renderers(ohlc_fig: Any):
    for renderer in ohlc_fig.renderers:
        glyph = getattr(renderer, "glyph", None)
        if glyph is None:
            continue
        if glyph.__class__.__name__ in {"Segment", "VBar"}:
            yield renderer, glyph


def _find_ohlc_figure(children: Iterable) -> Optional[Any]:
    for row in children:
        if row is None:
            continue
        cells = row if isinstance(row, (list, tuple)) else [row]
        for cell in cells:
            if cell is None or not hasattr(cell, "renderers"):
                continue
            for renderer, _ in _candlestick_renderers(cell):
                return cell
    return None


def _hide_candles_and_get_source(ohlc_fig: Any) -> Optional[ColumnDataSource]:
    source = None
    for renderer, _ in _candlestick_renderers(ohlc_fig):
        renderer.visible = False
        if source is None:
            source = renderer.data_source
    return source


def _ensure_ma1(source: ColumnDataSource) -> None:
    data = dict(source.data)
    if "MA1" in data:
        return
    close = np.array(data.get("Close", []), dtype=float)
    data["MA1"] = close.tolist()
    source.data = data


def _style_price_axis(ohlc_fig: Any) -> None:
    ohlc_fig.background_fill_color = BACKGROUND_COLOR
    ohlc_fig.border_fill_color = BACKGROUND_COLOR
    if ohlc_fig.legend:
        ohlc_fig.legend.visible = False


def _draw_dotted_ma(ohlc_fig: Any, source: ColumnDataSource, dash_pattern: Sequence[int], marker_step: int) -> None:
    dash = list(dash_pattern)
    ohlc_fig.line(
        "index",
        "MA1",
        source=source,
        line_color=LINE_COLOR,
        line_width=2.5,
        line_dash=dash,
        line_cap="round",
        line_join="round",
        legend_label="MA(1)",
    )
    if marker_step and marker_step > 1:
        indices = list(range(0, len(source.data.get("index", [])), marker_step))
        if indices:
            view = CDSView(filter=IndexFilter(indices))
            ohlc_fig.scatter(
                "index",
                "MA1",
                source=source,
                view=view,
                marker="circle",
                size=5,
                fill_color=LINE_COLOR,
                line_color=LINE_COLOR,
            )


def build_silver_candles(bt: Backtest):
    original_colors = plotting.BULL_COLOR, plotting.BEAR_COLOR
    try:
        plotting.BULL_COLOR, plotting.BEAR_COLOR = SILVER_BULL, SILVER_BEAR
        fig = bt.plot(open_browser=False)
    finally:
        plotting.BULL_COLOR, plotting.BEAR_COLOR = original_colors
    ohlc_fig = _find_ohlc_figure(fig.children)
    if ohlc_fig is not None:
        for _, glyph in _candlestick_renderers(ohlc_fig):
            if glyph.__class__.__name__ == "VBar":
                glyph.line_alpha = 0.0
            elif glyph.__class__.__name__ == "Segment":
                glyph.line_color = LINE_COLOR
                glyph.line_alpha = 0.85
    return fig


def build_ma_line(bt: Backtest):
    fig = bt.plot(open_browser=False)
    ohlc_fig = _find_ohlc_figure(fig.children)
    if ohlc_fig is not None:
        source = _hide_candles_and_get_source(ohlc_fig)
        if source is not None:
            _ensure_ma1(source)
            ohlc_fig.line(
                "index",
                "MA1",
                source=source,
                line_color=LINE_COLOR,
                line_width=2.5,
                legend_label="MA(1)",
            )
            _style_price_axis(ohlc_fig)
    return fig


def build_dotted_ma_line(bt: Backtest, dash_pattern: Sequence[int] | None = None, marker_step: int | None = None):
    fig = bt.plot(open_browser=False)
    ohlc_fig = _find_ohlc_figure(fig.children)
    if ohlc_fig is not None:
        source = _hide_candles_and_get_source(ohlc_fig)
        if source is not None:
            _ensure_ma1(source)
            _draw_dotted_ma(
                ohlc_fig,
                source,
                dash_pattern or DOTTED_DASH_PATTERN,
                marker_step or DOTTED_MARKER_STEP,
            )
            _style_price_axis(ohlc_fig)
    return fig


def display_bokeh(fig: Any) -> None:
    """Safely display a Bokeh figure inside notebooks."""
    html = file_html(fig, INLINE, "chart")
    display(HTML(html))


In [3]:
bt = prepare_backtest(sample_size=400)
bt

In [4]:
silver_fig = build_silver_candles(bt)
display_bokeh(silver_fig)

In [5]:
ma_fig = build_ma_line(bt)
display_bokeh(ma_fig)

In [6]:
dotted_fig = build_dotted_ma_line(bt, dash_pattern=(1, 18), marker_step=8)
display_bokeh(dotted_fig)